In [44]:
import folium
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np

from folium.plugins import *
from folium.features import *

import requests

In [45]:
df_raw = pd.read_csv("time_series_covid19_confirmed_global.csv")
df_raw.head()

EmptyDataError: No columns to parse from file

In [31]:
df = df_raw[(df_raw["Lat"]!=0) & (df_raw["Long"]!=0)]

In [32]:
m = folium.Map(location=[0, 0],tiles='Stamen Toner', zoom_start=1.5)
for index, row in df.iterrows():
    name = (row["Province/State"] + ", ") if type(row["Province/State"])==str else ""
    name += row["Country/Region"]
    folium.Circle(
        location = [row["Lat"],row["Long"]],
        radius = np.power(row["4/15/20"],0.5)*1000,
        popup = name,
        stroke = False,
        fill = True,
        fill_color = "dark_red"
    ).add_to(m)
m

In [33]:
dates = list(df.columns)[4:]

In [34]:
max_cases = (df.iloc[:,4:len(df.columns)]).max().max()
print(max_cases,type(max_cases))
df_norm = df.copy()
for d in dates:
    df_norm[d] = df_norm[d].multiply(1/max_cases)

732197 <class 'numpy.int64'>


In [35]:
df_data = []
for j in range(4,len(df.columns)):
    df_data.append([])
    for i in range(df.shape[0]):
        df_data[-1].append([df.iloc[i,2],df.iloc[i,3],df_norm.iloc[i,j]])
#[[[row["Lat"],row["Long"],row.iloc[i]] for index, row in df_cul] for i in range(5,len(df.columns))]

In [36]:
m_heat_time = folium.Map(location=[0, 0],tiles='Stamen Toner', zoom_start=1.5)
hm = HeatMapWithTime(data = list(reversed(df_data)), index = dates)
hm.add_to(m_heat_time)
m_heat_time

In [37]:
def create_geojson_features(df):
    print('> Creating GeoJSON features...')
    features = []
    for i in range(df.shape[0]):
        name = (df.iloc[i,0] + ", ") if type(df.iloc[i,0])==str else ""
        name += df.iloc[i,1]
        for j in range(4,df.shape[1]):
            newcases = df.iloc[i,j] - df.iloc[i,j-1] if j>4 else df.iloc[i,j]
            if df.iloc[i,j]>0:
                feature = {
                    'type': 'Feature',
                    'geometry': {
                        'type':'Point', 
                        'coordinates':[float(df.iloc[i,3]),float(df.iloc[i,2])]
                    },
                    'properties': {
                        'time': dates[j-4],
                        'style': {"opacity":0},
                        'icon': 'circle',
                        'iconstyle':{
                            'fillColor': "#ff0000",
                            'fillOpacity': 0.2,
                            'stroke': 'false',
                            'radius': int(np.power(df.iloc[i,j],0.25)*2)
                        },
                        "popup": name+":<br>"+str(newcases)+" new cases<br>"+str(df.iloc[i,j])+" culmulative",
                        "highlight": True 
                    },
                }
                features.append(feature)
    return features

In [38]:
def add_to_map(mp,features):    
    TimestampedGeoJson(
        {'type': 'FeatureCollection',
        'features': features}
        , period='P1D'
        , add_last_point=True
        , auto_play=False
        , loop=False
        , max_speed=24
        , transition_time = 1000/12
        , loop_button=True
        , date_options='DD/MM/YYYY'
        , time_slider_drag_update=True
        , duration = "P0D"
    ).add_to(mp)

In [39]:
features = create_geojson_features(df)
make_map(features)

> Creating GeoJSON features...
> Making map...
> Done.


In [40]:
def preprocess(df):
    print("> Preprocessing...")
    df_temp = df[(df["Lat"]!=0) & (df["Long"]!=0)]
    df_temp.sort_values(by="4/15/20",axis=0,ascending = False,inplace=True)
    return df_temp

In [41]:
def get_map(df):
    df_processed = preprocess(df)
    dates = list(df_processed.columns)[4:]
    features = create_geojson_features(df_processed)
    print('> Making map...')
    cases_map = folium.Map(location=[0,0], control_scale=True, zoom_start=1.5)
    m = make_map(features)
    print('> Done.')
    return m

In [42]:
res = get_map(df_raw)
res.save("COVID-19_cases_over_time.html")

> Preprocessing...
> Creating GeoJSON features...
> Making map...
> Done.


In [46]:
df_raw = pd.read_csv("https://data.humdata.org/hxlproxy/api/data-preview.csv?url=https%3A%2F%2Fraw.githubusercontent.com%2FCSSEGISandData%2FCOVID-19%2Fmaster%2Fcsse_covid_19_data%2Fcsse_covid_19_time_series%2Ftime_series_covid19_confirmed_global.csv&filename=time_series_covid19_confirmed_global.csv")
'''
data = {
    "searchTerm": "",
    "country": "",
    "sectoral_scope": "0",
    "recentProjects": "",
    "sort": "projectId",
    "dir": "DESC",
    "formatType": "csv"
}

file = requests.post("https://www.vcsprojectdatabase.org/services/publicViewServices/fetchProjectsExport", data)

with open("time_series_covid19_confirmed_global.csv", "wb+") as f:
    f.write(file.content)

page = requests.get(url)
with open("time_series_covid19_confirmed_global.csv","wb+") as f:
    f.write(page)

df_raw = pd.read_csv("time_series_covid19_confirmed_global.csv")
'''
res = get_map(df_raw)
res.save("COVID-19_cases_over_time.html")

> Preprocessing...
> Creating GeoJSON features...
> Making map...
> Done.
